In [1]:
import numpy as np 
import pandas as pd 
import itertools as it

# data visualization
import seaborn as sns
%matplotlib inline
from matplotlib import pyplot as plt
from matplotlib import style

# Algorithms
from sklearn import metrics
import xgboost as xgb
from xgboost import plot_tree
from sklearn.metrics import mean_squared_error, accuracy_score
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split, cross_val_score, KFold
from sklearn.metrics import roc_curve, auc, roc_auc_score

import warnings
warnings.filterwarnings("ignore")

Getting the Data

In [2]:
test_df = pd.read_csv("./titanic/test.csv")
train_df = pd.read_csv("./titanic/train.csv")

Data Exploration/Analysis

In [3]:
total = train_df.isnull().sum().sort_values(ascending=False)
percent_1 = train_df.isnull().sum()/train_df.isnull().count()*100
percent_2 = (round(percent_1, 1)).sort_values(ascending=False)
missing_data = pd.concat([total, percent_2], axis=1, keys=['Total', '%'])
missing_data.head(10)

Total     %
Cabin          687  77.1
Age            177  19.9
Embarked         2   0.2
PassengerId      0   0.0
Survived         0   0.0
Pclass           0   0.0
Name             0   0.0
Sex              0   0.0
SibSp            0   0.0
Parch            0   0.0

The Embarked feature has only 2 missing values, which can easily be filled. It will be much more tricky, to deal with the ‘Age’ feature, which has 177 missing values. The ‘Cabin’ feature needs further investigation, but it looks like that we might want to drop it from the dataset, since 77 % of it are missing.

In [4]:
train_df.columns.values

array(['PassengerId', 'Survived', 'Pclass', 'Name', 'Sex', 'Age', 'SibSp',
       'Parch', 'Ticket', 'Fare', 'Cabin', 'Embarked'], dtype=object)

### Data Preprocessing

First, I will drop ‘PassengerId’ from the train set, because it does not contribute to a persons survival probability. I will not drop it from the test set, since it is required there for the submission.

In [5]:
train_df = train_df.drop(['PassengerId'], axis=1)

In [6]:
# extracting and then removing the targets from the training data 
targets = train_df['Survived']
train_df.drop(['Survived'], 1, inplace=True)

In [7]:
train_df

Pclass                                               Name     Sex   Age  \
0         3                            Braund, Mr. Owen Harris    male  22.0   
1         1  Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0   
2         3                             Heikkinen, Miss. Laina  female  26.0   
3         1       Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0   
4         3                           Allen, Mr. William Henry    male  35.0   
..      ...                                                ...     ...   ...   
886       2                              Montvila, Rev. Juozas    male  27.0   
887       1                       Graham, Miss. Margaret Edith  female  19.0   
888       3           Johnston, Miss. Catherine Helen "Carrie"  female   NaN   
889       1                              Behr, Mr. Karl Howell    male  26.0   
890       3                                Dooley, Mr. Patrick    male  32.0   

     SibSp  Parch            Ticket     Fare Cabin Embarked  
0        1      0         A/5 21171   7.2500   NaN        S  
1        1      0          PC 17599  71.2833   C85        C  
2        0      0  STON/O2. 3101282   7.9250   NaN        S  
3        1      0            113803  53.1000  C123        S  
4        0      0            373450   8.0500   NaN        S  
..     ...    ...               ...      ...   ...      ...  
886      0      0            211536  13.0000   NaN        S  
887      0      0            112053  30.0000   B42        S  
888      1      2        W./C. 6607  23.4500   NaN        S  
889      0      0            111369  30.0000  C148        C  
890      0      0            370376   7.7500   NaN        Q  

[891 rows x 10 columns]

In [8]:
test_df

PassengerId  Pclass                                          Name  \
0            892       3                              Kelly, Mr. James   
1            893       3              Wilkes, Mrs. James (Ellen Needs)   
2            894       2                     Myles, Mr. Thomas Francis   
3            895       3                              Wirz, Mr. Albert   
4            896       3  Hirvonen, Mrs. Alexander (Helga E Lindqvist)   
..           ...     ...                                           ...   
413         1305       3                            Spector, Mr. Woolf   
414         1306       1                  Oliva y Ocana, Dona. Fermina   
415         1307       3                  Saether, Mr. Simon Sivertsen   
416         1308       3                           Ware, Mr. Frederick   
417         1309       3                      Peter, Master. Michael J   

        Sex   Age  SibSp  Parch              Ticket      Fare Cabin Embarked  
0      male  34.5      0      0              330911    7.8292   NaN        Q  
1    female  47.0      1      0              363272    7.0000   NaN        S  
2      male  62.0      0      0              240276    9.6875   NaN        Q  
3      male  27.0      0      0              315154    8.6625   NaN        S  
4    female  22.0      1      1             3101298   12.2875   NaN        S  
..      ...   ...    ...    ...                 ...       ...   ...      ...  
413    male   NaN      0      0           A.5. 3236    8.0500   NaN        S  
414  female  39.0      0      0            PC 17758  108.9000  C105        C  
415    male  38.5      0      0  SOTON/O.Q. 3101262    7.2500   NaN        S  
416    male   NaN      0      0              359309    8.0500   NaN        S  
417    male   NaN      1      1                2668   22.3583   NaN        C  

[418 rows x 11 columns]

In [9]:
# merging train data and test data for future feature engineering
# we'll also remove the PassengerID since this is not an informative feature
combined = train_df.append(test_df)
combined.reset_index(inplace=True)
combined.drop(['index', 'PassengerId'], inplace=True, axis=1)

In [10]:
combined

Pclass                                               Name     Sex   Age  \
0          3                            Braund, Mr. Owen Harris    male  22.0   
1          1  Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0   
2          3                             Heikkinen, Miss. Laina  female  26.0   
3          1       Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0   
4          3                           Allen, Mr. William Henry    male  35.0   
...      ...                                                ...     ...   ...   
1304       3                                 Spector, Mr. Woolf    male   NaN   
1305       1                       Oliva y Ocana, Dona. Fermina  female  39.0   
1306       3                       Saether, Mr. Simon Sivertsen    male  38.5   
1307       3                                Ware, Mr. Frederick    male   NaN   
1308       3                           Peter, Master. Michael J    male   NaN   

      SibSp  Parch              Ticket      Fare Cabin Embarked  
0         1      0           A/5 21171    7.2500   NaN        S  
1         1      0            PC 17599   71.2833   C85        C  
2         0      0    STON/O2. 3101282    7.9250   NaN        S  
3         1      0              113803   53.1000  C123        S  
4         0      0              373450    8.0500   NaN        S  
...     ...    ...                 ...       ...   ...      ...  
1304      0      0           A.5. 3236    8.0500   NaN        S  
1305      0      0            PC 17758  108.9000  C105        C  
1306      0      0  SOTON/O.Q. 3101262    7.2500   NaN        S  
1307      0      0              359309    8.0500   NaN        S  
1308      1      1                2668   22.3583   NaN        C  

[1309 rows x 10 columns]

In [11]:
#Now let's map the title can bin them
Title_Dictionary = {
    "Capt": "Officer",
    "Col": "Officer",
    "Major": "Officer",
    "Jonkheer": "Royalty",
    "Don": "Royalty",
    "Dona": "Royalty",
    "Sir" : "Royalty",
    "Dr": "Officer",
    "Rev": "Officer",
    "the Countess":"Royalty",
    "Mme": "Mrs",
    "Mlle": "Miss",
    "Ms": "Mrs",
    "Mr" : "Mr",
    "Mrs" : "Mrs",
    "Miss" : "Miss",
    "Master" : "Master",
    "Lady" : "Royalty"
}

In [12]:
#Generate a new Title column
combined['Title'] = combined['Name'].map(lambda name:name.split(',')[1].split('.')[0].strip())
combined['Title'] = combined['Title'].map(Title_Dictionary)

In [13]:
#let's get the median age based on people's gender, Pclass and Title
fill_mean = lambda g: g.fillna(g.mean())
combined['Age'] = combined.groupby(['Sex', 'Title', 'Pclass'])['Age'].apply(fill_mean)

In [14]:
combined

Pclass                                               Name     Sex  \
0          3                            Braund, Mr. Owen Harris    male   
1          1  Cumings, Mrs. John Bradley (Florence Briggs Th...  female   
2          3                             Heikkinen, Miss. Laina  female   
3          1       Futrelle, Mrs. Jacques Heath (Lily May Peel)  female   
4          3                           Allen, Mr. William Henry    male   
...      ...                                                ...     ...   
1304       3                                 Spector, Mr. Woolf    male   
1305       1                       Oliva y Ocana, Dona. Fermina  female   
1306       3                       Saether, Mr. Simon Sivertsen    male   
1307       3                                Ware, Mr. Frederick    male   
1308       3                           Peter, Master. Michael J    male   

           Age  SibSp  Parch              Ticket      Fare Cabin Embarked  \
0     22.00000      1      0           A/5 21171    7.2500   NaN        S   
1     38.00000      1      0            PC 17599   71.2833   C85        C   
2     26.00000      0      0    STON/O2. 3101282    7.9250   NaN        S   
3     35.00000      1      0              113803   53.1000  C123        S   
4     35.00000      0      0              373450    8.0500   NaN        S   
...        ...    ...    ...                 ...       ...   ...      ...   
1304  28.31891      0      0           A.5. 3236    8.0500   NaN        S   
1305  39.00000      0      0            PC 17758  108.9000  C105        C   
1306  38.50000      0      0  SOTON/O.Q. 3101262    7.2500   NaN        S   
1307  28.31891      0      0              359309    8.0500   NaN        S   
1308   6.09000      1      1                2668   22.3583   NaN        C   

        Title  
0          Mr  
1         Mrs  
2        Miss  
3         Mrs  
4          Mr  
...       ...  
1304       Mr  
1305  Royalty  
1306       Mr  
1307       Mr  
1308   Master  

[1309 rows x 11 columns]

In [15]:
# Name can be dropped now
combined.drop('Name', axis=1, inplace=True)

In [16]:
# removing the title variable
combined.drop('Title', axis=1, inplace=True)

In [17]:
# removing the Cabin variable
combined.drop('Cabin', axis=1, inplace=True)

In [18]:
# removing the Ticket variable
combined.drop('Ticket', axis=1, inplace=True)

In [19]:
#Fill out the missing fare data
combined['Fare'].fillna(combined['Fare'].mean(), inplace=True)

In [20]:
# two missing embarked values - filling them with the most frequent one in the train set
combined['Embarked'].fillna('S', inplace=True)

In [21]:
# encoding in dummy variable
embarked_dummies = pd.get_dummies(combined['Embarked'], prefix='Embarked')
combined = pd.concat([combined, embarked_dummies], axis=1)
combined

Pclass     Sex       Age  SibSp  Parch      Fare Embarked  Embarked_C  \
0          3    male  22.00000      1      0    7.2500        S           0   
1          1  female  38.00000      1      0   71.2833        C           1   
2          3  female  26.00000      0      0    7.9250        S           0   
3          1  female  35.00000      1      0   53.1000        S           0   
4          3    male  35.00000      0      0    8.0500        S           0   
...      ...     ...       ...    ...    ...       ...      ...         ...   
1304       3    male  28.31891      0      0    8.0500        S           0   
1305       1  female  39.00000      0      0  108.9000        C           1   
1306       3    male  38.50000      0      0    7.2500        S           0   
1307       3    male  28.31891      0      0    8.0500        S           0   
1308       3    male   6.09000      1      1   22.3583        C           1   

      Embarked_Q  Embarked_S  
0              0           1  
1              0           0  
2              0           1  
3              0           1  
4              0           1  
...          ...         ...  
1304           0           1  
1305           0           0  
1306           0           1  
1307           0           1  
1308           0           0  

[1309 rows x 10 columns]

In [22]:
combined.drop('Embarked', axis=1, inplace=True)

In [23]:
# mapping gender to numerical one 
combined['Sex'] = combined['Sex'].map({'male':1, 'female':0})

In [24]:
# introducing a new feature : the size of families (including the passenger)
combined['FamilySize'] = combined['Parch'] + combined['SibSp'] + 1

In [25]:
combined

Pclass  Sex       Age  SibSp  Parch      Fare  Embarked_C  Embarked_Q  \
0          3    1  22.00000      1      0    7.2500           0           0   
1          1    0  38.00000      1      0   71.2833           1           0   
2          3    0  26.00000      0      0    7.9250           0           0   
3          1    0  35.00000      1      0   53.1000           0           0   
4          3    1  35.00000      0      0    8.0500           0           0   
...      ...  ...       ...    ...    ...       ...         ...         ...   
1304       3    1  28.31891      0      0    8.0500           0           0   
1305       1    0  39.00000      0      0  108.9000           1           0   
1306       3    1  38.50000      0      0    7.2500           0           0   
1307       3    1  28.31891      0      0    8.0500           0           0   
1308       3    1   6.09000      1      1   22.3583           1           0   

      Embarked_S  FamilySize  
0              1           2  
1              0           2  
2              1           1  
3              1           2  
4              1           1  
...          ...         ...  
1304           1           1  
1305           0           1  
1306           1           1  
1307           1           1  
1308           0           3  

[1309 rows x 10 columns]

### Modelling preparing

In [26]:
#Prepare the training dataset
X = combined.iloc[:891]
y = targets

In [27]:
X_train, X_test, y_train,  y_test = train_test_split(X, y, test_size = 0.2, random_state=5)

In [28]:
xgb_train = xgb.DMatrix(data=X_train,label=y_train)
xgb_test = xgb.DMatrix(data=X_test,label=y_test)

In [29]:
params={
'booster':'gbtree',
'objective': 'multi:softmax', #多分类的问题
'num_class':10, # 类别数，与 multisoftmax 并用
'gamma':0.1,  # 用于控制是否后剪枝的参数,越大越保守，一般0.1、0.2这样子。
'max_depth':12, # 构建树的深度，越大越容易过拟合
'lambda':2,  # 控制模型复杂度的权重值的L2正则化项参数，参数越大，模型越不容易过拟合。
'subsample':0.7, # 随机采样训练样本
'colsample_bytree':0.7, # 生成树时进行的列采样
'min_child_weight':3, 
# 这个参数默认是 1，是每个叶子里面 h 的和至少是多少，对正负样本不均衡时的 0-1 分类而言
#，假设 h 在 0.01 附近，min_child_weight 为 1 意味着叶子节点中最少需要包含 100 个样本。
#这个参数非常影响结果，控制叶子节点中二阶导的和的最小值，该参数值越小，越容易 overfitting。 
'silent':0 ,#设置成1则没有运行信息输出，最好是设置为0.
'eta': 0.007, # 如同学习率
'seed':1000,
'nthread':7,# cpu 线程数
#'eval_metric': 'auc'
}

plst = list(params.items())
num_rounds = 5000

In [30]:
xg_model = xgb.train(params=plst, dtrain=xgb_train, num_boost_round=num_rounds)

[18:34:18] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parameters: { silent } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[18:34:18] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'multi:softmax' was changed from 'merror' to 'mlogloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


In [31]:
preds = xg_model.predict(xgb_test,ntree_limit=xg_model.best_ntree_limit)
preds

array([0., 0., 0., 0., 0., 0., 1., 0., 1., 0., 1., 0., 0., 1., 0., 1., 0.,
       0., 0., 0., 0., 1., 1., 1., 0., 1., 0., 0., 0., 0., 0., 1., 1., 0.,
       1., 1., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 1., 1., 1., 0., 0.,
       1., 1., 0., 0., 0., 1., 0., 0., 1., 0., 0., 0., 0., 1., 0., 0., 0.,
       0., 0., 1., 0., 1., 0., 1., 0., 0., 0., 1., 1., 0., 0., 0., 0., 1.,
       1., 0., 1., 0., 0., 0., 0., 1., 0., 1., 0., 1., 0., 0., 0., 1., 1.,
       0., 0., 1., 1., 0., 0., 0., 0., 0., 0., 0., 0., 1., 1., 1., 0., 1.,
       0., 0., 0., 0., 1., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0.,
       0., 0., 0., 0., 0., 0., 0., 1., 0., 1., 1., 1., 0., 0., 1., 0., 0.,
       0., 0., 1., 1., 0., 0., 0., 0., 0., 1., 0., 1., 0., 1., 0., 0., 0.,
       1., 0., 1., 1., 0., 0., 0., 1., 0.], dtype=float32)

In [32]:
acc = accuracy_score(y_test, preds)
print("Accuracy: %.2f%%" % (acc * 100.0))

Accuracy: 81.01%


## Cross Validation

In [37]:
param_grid = {
             'gamma':[0,0.1,0.2], 
             'max_depth':[6,8,12],
             'lambda':[1,2,4],
             'subsample':[0.5,0.7],
             'colsample_bytree':[0.5,0.7], 
             'min_child_weight':[1,2,3],
             'eta': [0.08,0.1,0.2]
            }

In [38]:
s = sorted(param_grid)
print(s)
combination = it.product(*(param_grid[Name] for Name in s))
ls = list(combination)


['colsample_bytree', 'eta', 'gamma', 'lambda', 'max_depth', 'min_child_weight', 'subsample']


In [39]:
def kfold_index(X_train, k):
    if k < 1:
        print("K cannot be smaller than 1.")
    else:
        l = X_train.shape[0]
        tail = l % k
        q = l // k
        index = [0]
        output_index = []
        
        for i in range(1, tail):
            index.append(i*q + 1)
        for j in range(tail, k+1):
            index.append(j*q + tail)
        for m in range(len(index) - 1):
            output_index.append([index[m], index[m+1]])
        
        return output_index

In [48]:
def cv(X_train, y_train, params, num_rounds, early_stopping_rounds, k):
    index = kfold_index(X_train, k)
    
    auc_score = []
    br = []
    for i in range(k):
        cv_xtest = X_train.iloc[index[i][0]:index[i][1],:]
        cv_ytest = y_train.iloc[index[i][0]:index[i][1],]

        cv_xtrain = X_train.drop(X_train.index[index[i][0]:index[i][1]])
        cv_ytrain = y_train.drop(y_train.index[index[i][0]:index[i][1]])

        xgb_train = xgb.DMatrix(data=cv_xtrain,label=cv_ytrain)
        xgb_test = xgb.DMatrix(data=cv_xtest,label=cv_ytest)


        xgb_model = xgb.train(params=params, 
                              dtrain=xgb_train, 
                              num_boost_round=num_rounds, 
                              early_stopping_rounds=early_stopping_rounds, 
                              evals=[(xgb_test, "test_evalset")],
                              verbose_eval=False)
        
        fpr, tpr, thresholds = metrics.roc_curve(cv_ytest, xgb_model.predict(xgb_test))
        acc = metrics.auc(fpr, tpr)
        auc_score.append(acc)
        
        # get number of boosting round
        bb = xgb_model.best_iteration
        br.append(bb)
   

    return np.mean(auc_score), np.mean(br)

In [49]:
for i in ls:

    params={
        'booster':'gbtree',
        'objective':'binary:logistic',
        'gamma':i[2], 
        'max_depth':i[4],
        'lambda':i[3], 
        'subsample':i[6],
        'colsample_bytree':i[0],
        'min_child_weight':i[5], 
        'silent':0,
        'eta': i[1],
        'seed':1000,
        'nthread':6
    }
    plst = list(params.items())
    num_rounds = 1000
    early_stopping_rounds = 30
    
    sc, num_round = cv(X_train, y_train, params=plst, num_rounds=num_rounds, early_stopping_rounds=early_stopping_rounds, k=10)

    result = 0
    if sc >= result:
        result = sc
        parameter = i
        mean_num_round = num_round
        
print(result, mean_num_round, parameter)

[18:56:26] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parameters: { silent } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[18:56:26] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[18:56:26] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parameters: { silent } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[18:56

[18:56:26] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parameters: { silent } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[18:56:26] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[18:56:26] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parameters: { silent } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[18:56

[18:56:27] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parameters: { silent } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[18:56:27] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[18:56:27] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parameters: { silent } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[18:56

[18:56:28] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parameters: { silent } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[18:56:28] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[18:56:28] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parameters: { silent } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[18:56

[18:56:29] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parameters: { silent } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[18:56:29] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[18:56:29] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parameters: { silent } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[18:56

...

[19:03:57] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[19:03:57] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parameters: { silent } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[19:03:57] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[19:03:57] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parame

[19:03:58] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parameters: { silent } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[19:03:58] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[19:03:58] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parameters: { silent } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[19:03

[19:03:58] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parameters: { silent } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[19:03:58] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[19:03:58] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parameters: { silent } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[19:03

[19:03:59] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parameters: { silent } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[19:03:59] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
[19:03:59] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parameters: { silent } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[19:03

[19:04:00] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parameters: { silent } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[19:04:00] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.
0.8644293239834082 41.0 (0.7, 0.2, 0.2, 4, 12, 3, 0.7)


In [50]:
print(result, mean_num_round, parameter)

0.8644293239834082 41.0 (0.7, 0.2, 0.2, 4, 12, 3, 0.7)


In [51]:
best_param = {
        'booster':'gbtree',
        'objective':'binary:logistic',
        'gamma':parameter[2], 
        'max_depth':parameter[4],
        'lambda':parameter[3], 
        'subsample':parameter[6],
        'colsample_bytree':parameter[0],
        'min_child_weight':parameter[5], 
        'silent':0,
        'eta': parameter[1],
        'seed':1000,
        'nthread':6
    }

In [53]:
xg_model = xgb.train(params=best_param, 
                     dtrain=xgb_train, 
                     num_boost_round=1000, 
                     early_stopping_rounds=30, 
                     evals=[(xgb_test, "test_evalset")],
                     verbose_eval=False)

[19:10:47] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:541: 
Parameters: { silent } might not be used.

  This may not be accurate due to some parameters are only used in language bindings but
  passed down to XGBoost core.  Or some parameters are not used but slip through this
  verification. Please open an issue if you find above cases.


[19:10:47] WARNING: /Users/travis/build/dmlc/xgboost/src/learner.cc:1061: Starting in XGBoost 1.3.0, the default evaluation metric used with the objective 'binary:logistic' was changed from 'error' to 'logloss'. Explicitly set eval_metric if you'd like to restore the old behavior.


In [57]:
fpr, tpr, thresholds = metrics.roc_curve(y_test, xg_model.predict(xgb_test))
acc = metrics.auc(fpr, tpr)
print(acc)

0.8946078431372549
